# 🎵 Music Dataset Vectorization and Hybrid Search Workshop

Welcome to this hands-on workshop! In this session, we'll walk through the process of preparing, vectorizing, and inserting a music dataset into an Elasticsearch index for hybrid search (vector + metadata). Let’s dive in!

## 1. 📦 Import Required Modules

We begin by importing the necessary libraries for data handling, transformation, and integration.

In [5]:
import os
import pandas as pd
from glob import glob
import torch
from panns_inference import AudioTagging
from qdrant_client import QdrantClient
from qdrant_client.http import models
from utils.audio import download_kaggle_dataset, generate_random_dataset

/Users/julian_castro/Documents/projects/audio_app/.venv/lib/python3.10/site-packages/pydub/utils.py:170: RuntimeWarning: Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work
  warn("Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work", RuntimeWarning)


## 2. 📥 Download the Dataset

We use the `download_kaggle_dataset()` function to fetch a Kaggle dataset that contains music metadata and `.mp3` audio files. This dataset includes genres such as *latin*, *pop*, *reggae*, *rock*, *electronic*, and more.


In [ ]:
download_kaggle_dataset("jorgeruizdev/ludwig-music-dataset-moods-and-subgenres")

## 3. 🎲 Generate a Balanced Subset

We'll create a random, balanced dataset of **130 songs per genre** using the full dataset. This ensures fair representation for each music genre in our analysis.

In [41]:
genres = ["latin", "pop", "reggae", "rock", "electronic"]
data_set = generate_random_dataset(genres, 130)
print(type(data_set))
item = data_set[0]
item

Loading latin...
Loading pop...
Loading reggae...
Loading rock...
Loading electronic...
<class 'datasets.arrow_dataset.Dataset'>


{'audio': {'path': '/Users/julian_castro/Documents/projects/audio_app/data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/electronic/0vsOxIBK36keLH8Bezie9A.mp3',
  'array': array([ 0.00000000e+00, -8.69972094e-09, -4.86083040e-09, ...,
         -1.59396112e-01, -1.23613618e-01, -1.67727619e-01]),
  'sampling_rate': 44100}}

## 4. 🆔 Extract Item IDs

Each item in the dataset has a unique identifier. We'll extract these IDs to reference songs throughout our workflow.

In [43]:
ids = [
    (data_set[i]["audio"]["path"].split("/")[-1].replace(".mp3", ""))
    for i in range(len(data_set))
]

index = [num for num in range(len(data_set))]
ids[:4]

['0vsOxIBK36keLH8Bezie9A',
 '0jmfiZP6MBtrORE1vpvFWU',
 '3ddxZzCKZpTObDygewlwXB',
 '3GCucY8KSMS80NEU0ey0by']

## 5. 🧾 Add Index and ID Columns

To maintain consistency, we append an `index` and `id` column to the dataset for efficient lookups and merges later on.

In [44]:
data_set = data_set.add_column("index", index)
data_set = data_set.add_column("id", ids)
data_set[-1]
data_set[-1].keys()

dict_keys(['audio', 'index', 'id'])

## 6. 📄 Load Labels (Large JSON File)

We’ll load a large JSON file containing labels (e.g., genre, mood, artist info) using `pandas.read_json()`. These labels will enrich our dataset with valuable metadata.

In [45]:
label_path = "./../data/ludwig-music-dataset-moods-and-subgenres/labels.json"
labels = pd.read_json(label_path)
labels.head()

tracks
35ecMLCJ1x2giJuvHLrI1t  {'otherSubgenres': {'L': [{'S': 'electronic---...
3p0EUhkUeCNrBIZwkjmeYe  {'otherSubgenres': {'L': []}, 'artist': {'S': ...
0rb6HvdvWJRkyhxsfFf1ep  {'otherSubgenres': {'L': [{'S': 'rock'}, {'S':...
4ssD5IkaicvM3L2Ff8FPWQ  {'otherSubgenres': {'L': []}, 'artist': {'S': ...
586ncAs8cYRTBlrxMDfmSP  {'otherSubgenres': {'L': [{'S': 'electronic---...

## 7. 🧠 Extract Metadata for Each Item

From the main dataset, we extract relevant metadata (e.g., artist, release date, tempo, key, etc.) for each song. This data will later be used in hybrid search.

In [46]:
def get_metadata(item: dict) -> pd.Series:
    cols = ["artist", "genre", "name", "subgenres", "sad", "happy", "party", "popularity"]
    list_of_cols = []
    for col in cols:
        try:
            mdata = list(item[col].values())[0]
        except:
            mdata = "Unknown"
        list_of_cols.append(mdata)
    
    return pd.Series(list_of_cols, index=cols)


labels = labels["tracks"].apply(get_metadata).reset_index()
labels.head()

index         artist        genre  \
0  35ecMLCJ1x2giJuvHLrI1t        Riovolt   electronic   
1  3p0EUhkUeCNrBIZwkjmeYe  R.L. Burnside        blues   
2  0rb6HvdvWJRkyhxsfFf1ep   Chapterhouse         rock   
3  4ssD5IkaicvM3L2Ff8FPWQ  Lowell Fulsom  funk / soul   
4  586ncAs8cYRTBlrxMDfmSP     Paul Ellis   electronic   

                            name  \
0  It Ain't Over 'till It's Over   
1          Fireman Ring the Bell   
2                   Falling Down   
3                          Tramp   
4                       Dissolve   

                                           subgenres              sad  \
0  [{'S': 'electronic---ambient'}, {'S': 'electro...   0.808553755283   
1                   [{'S': 'blues---country blues'}]   0.192250967026   
2                         [{'S': 'rock---shoegaze'}]  0.0304505825043   
3            [{'S': 'funk / soul---rhythm & blues'}]   0.584066450596   
4                    [{'S': 'electronic---ambient'}]   0.515594601631   

            happy              party popularity  
0  0.117319412529    0.0187958143651         31  
1  0.589263141155  0.000199172980501         30  
2  0.447863191366     0.909360527992         36  
3  0.448383301497      0.19365106523         30  
4  0.371642351151    0.0393997617066          0

## 8. 🎶 Extract Subgenres

In addition to top-level genres, we parse out **subgenres** for more granular classification and analysis.

In [47]:
def get_vals_from_subgenres(genres: list) -> list:
    genre_list = []
    for d in genres:
        if type(d) != str:
            for _, val in d.items():
                genre_list.append(val)
    
    return genre_list

labels["subgenres"] = labels["subgenres"].apply(get_vals_from_subgenres)
labels["subgenres"].head()

0    [electronic---ambient, electronic---downtempo,...
1                              [blues---country blues]
2                                    [rock---shoegaze]
3                       [funk / soul---rhythm & blues]
4                               [electronic---ambient]
Name: subgenres, dtype: object

## 9. 📁 Extract File Paths for Audio Files

We collect the paths to the actual `.mp3` files. These will be used later when generating audio embeddings.


In [48]:
files = []
for genre in genres:
    files_path = os.path.join("./../data/ludwig-music-dataset-moods-and-subgenres", "mp3", "mp3", genre, "*.mp3")
    genre_files = glob(files_path)
    files.extend(genre_files)

ids = [file.split("/")[-1].replace(".mp3", "") for file in files]
music_paths = pd.DataFrame(zip(ids, files), columns=["id", "url"])
music_paths.head()

id                                                url
0  5f1SjUy6ySgaEUIIy2m9l4  ./../data/ludwig-music-dataset-moods-and-subge...
1  03tbpnBQ9kiAL8GX0ouZUG  ./../data/ludwig-music-dataset-moods-and-subge...
2  67wqhzuPtGbZNYG1eVoLsd  ./../data/ludwig-music-dataset-moods-and-subge...
3  0YfDtPub9AsTu4278mDWJE  ./../data/ludwig-music-dataset-moods-and-subge...
4  7vH4D94WWhAdjll6b62wiw  ./../data/ludwig-music-dataset-moods-and-subge...

## 10. 🔗 Merge Metadata, Labels & Paths

We combine all the extracted information into a single DataFrame using a multi-step merge operation:

In [49]:
metadata = data_set.select_columns(["index", "id"]) \
    .to_pandas() \
    .merge(right=labels, how="left", left_on="id", right_on="index") \
    .merge(right=music_paths, how="left", left_on="id", right_on="id") \
    .drop("index_y", axis=1) \
    .rename({"index_x": "index"}, axis=1)

metadata.head()

index                      id             artist       genre  \
0      0  0vsOxIBK36keLH8Bezie9A           Pendulum  electronic   
1      1  0jmfiZP6MBtrORE1vpvFWU  Nightmares On Wax  electronic   
2      2  3ddxZzCKZpTObDygewlwXB         Slow Magic  electronic   
3      3  3GCucY8KSMS80NEU0ey0by           Pendulum  electronic   
4      4  12BJTGESsHRonZSBGw9XXi            P-Model  electronic   

             name                                          subgenres  \
0       Different                         [electronic---drum n bass]   
1        Be, I Do  [electronic---downtempo, electronic---trip hop...   
2      Waited 4 U                             [electronic---electro]   
3  The Other Side                         [electronic---drum n bass]   
4   Goes on Ghost  [electronic---electro, electronic---new wave, ...   

              sad           happy            party popularity  \
0  0.159620672464  0.257579416037   0.977688491344         41   
1  0.313051044941  0.187118664384   0.399286955595         44   
2  0.608639240265  0.105242662132  0.0857971906662         55   
3  0.209101587534  0.158047914505   0.991388976574         46   
4  0.680889248848  0.449430823326   0.170126751065          7   

                                                 url  
0  ./../data/ludwig-music-dataset-moods-and-subge...  
1  ./../data/ludwig-music-dataset-moods-and-subge...  
2  ./../data/ludwig-music-dataset-moods-and-subge...  
3  ./../data/ludwig-music-dataset-moods-and-subge...  
4  ./../data/ludwig-music-dataset-moods-and-subge...

## 11. 📦 Prepare Payloads for Vectorization

We prepare input payloads (e.g., file paths, metadata) to be passed to the embedding model. These payloads are structured so each song can be converted into a vector representation.

In [59]:
payload = metadata.drop(["index", "id"], axis=1).to_dict(orient="records")
payload[:3]

[{'artist': 'Pendulum',
  'genre': 'electronic',
  'name': 'Different',
  'subgenres': ['electronic---drum n bass'],
  'sad': '0.159620672464',
  'happy': '0.257579416037',
  'party': '0.977688491344',
  'popularity': '41',
  'url': './../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/electronic/0vsOxIBK36keLH8Bezie9A.mp3'},
 {'artist': 'Nightmares On Wax',
  'genre': 'electronic',
  'name': 'Be, I Do',
  'subgenres': ['electronic---downtempo',
   'electronic---trip hop',
   'hip hop---trip hop'],
  'sad': '0.313051044941',
  'happy': '0.187118664384',
  'party': '0.399286955595',
  'popularity': '44',
  'url': './../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/electronic/0jmfiZP6MBtrORE1vpvFWU.mp3'},
 {'artist': 'Slow Magic',
  'genre': 'electronic',
  'name': 'Waited 4 U',
  'subgenres': ['electronic---electro'],
  'sad': '0.608639240265',
  'happy': '0.105242662132',
  'party': '0.0857971906662',
  'popularity': '55',
  'url': './../data/ludwig-music-dataset-moods-an

## 12. 🧬 Generate Embeddings

We use an audio embedding model (e.g., Wav2Vec2, VGGish) to convert each song into a vector. This step captures the audio’s semantic content for similarity search.

In [37]:
data_set.to_pandas().head().keys()

Index(['audio', 'index', 'id'], dtype='object')

In [71]:
from utils.audio import get_audio_data

model = "facebook/wav2vec2-base-960h"

def get_embeddings(batch: dict):
    embeddings = []
    for _id, _index in zip(batch["id"], batch["index"]):
        _genre = metadata.iloc[_index]["genre"]
        try:
            audio_data = get_audio_data(_id, _genre, model)
            embeddings.append(audio_data["embeddings"])
        except FileNotFoundError:
            print(f"File not found for id: {_id}, genre: {_genre}. Skipping.")
            embeddings.append(None)
    
    batch["embeddings"] = embeddings
    return batch


with torch.inference_mode():
    data_set = data_set.map(get_embeddings, batched=True, batch_size=8)

Map:   0%|          | 0/650 [00:00<?, ? examples/s]

Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/electronic/0vsOxIBK36keLH8Bezie9A.mp3 with shape (479818,)
Extracting embeddings from /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/electronic/0vsOxIBK36keLH8Bezie9A.mp3...
With device: mps


Some weights of Wav2Vec2Model were not initialized from the model checkpoint at facebook/wav2vec2-base-960h and are newly initialized: ['masked_spec_embed']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/electronic/0vsOxIBK36keLH8Bezie9A.mp3 with shape (479818,)
Audio tensor shape: (479818,)
Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/electronic/0jmfiZP6MBtrORE1vpvFWU.mp3 with shape (479818,)
Extracting embeddings from /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/electronic/0jmfiZP6MBtrORE1vpvFWU.mp3...
With device: mps


Some weights of Wav2Vec2Model were not initialized from the model checkpoint at facebook/wav2vec2-base-960h and are newly initialized: ['masked_spec_embed']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


...

Some weights of Wav2Vec2Model were not initialized from the model checkpoint at facebook/wav2vec2-base-960h and are newly initialized: ['masked_spec_embed']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/5N9UaSO64vYxZKO25eNiy0.mp3 with shape (479818,)
Audio tensor shape: (479818,)
Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/6K5UtSAXChS6Rpm2NZJnrF.mp3 with shape (479818,)
Extracting embeddings from /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/6K5UtSAXChS6Rpm2NZJnrF.mp3...
With device: mps
Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/6K5UtSAXChS6Rpm2NZJnrF.mp3 with shape (479818,)
Extracting embeddings from /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/6K5UtSAXChS6Rpm2NZJnrF.mp3...
With device: m

Some weights of Wav2Vec2Model were not initialized from the model checkpoint at facebook/wav2vec2-base-960h and are newly initialized: ['masked_spec_embed']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/6K5UtSAXChS6Rpm2NZJnrF.mp3 with shape (479818,)
Audio tensor shape: (479818,)


Map: 100%|██████████| 650/650 [36:04<00:00,  3.33s/ examples]


In [72]:
data_set.to_pandas().head()

audio  index  \
0  {'bytes': None, 'path': '/Users/julian_castro/...      0   
1  {'bytes': None, 'path': '/Users/julian_castro/...      1   
2  {'bytes': None, 'path': '/Users/julian_castro/...      2   
3  {'bytes': None, 'path': '/Users/julian_castro/...      3   
4  {'bytes': None, 'path': '/Users/julian_castro/...      4   

                       id                                         embeddings  
0  0vsOxIBK36keLH8Bezie9A  [-0.038435087, 0.027751371, 0.0071876473, -0.0...  
1  0jmfiZP6MBtrORE1vpvFWU  [0.0025360596, 0.014639635, -0.055600327, -0.0...  
2  3ddxZzCKZpTObDygewlwXB  [-0.013173088, 0.023973426, -0.07701268, -0.05...  
3  3GCucY8KSMS80NEU0ey0by  [-0.09957058, 0.056793876, -0.011628009, -0.01...  
4  12BJTGESsHRonZSBGw9XXi  [-0.078394376, 0.030760014, -0.027152231, -0.0...

## 13. 🌐 Connect to Elasticsearch

We establish a connection to an Elasticsearch instance where we'll index all vector and metadata documents. This will enable powerful hybrid search capabilities, combining traditional filters and vector similarity.


In [76]:
from elasticsearch import Elasticsearch, helpers

es = Elasticsearch(
    ['http://localhost:9200'],
    http_auth=('elastic', 'test_password'),
    verify_certs=False
)

INDEX_NAME = "music_embeddings"
if es.indices.exists(index=INDEX_NAME):
    es.indices.delete(index=INDEX_NAME)

# Create index with mapping for vector data and metadata
es.indices.create(
    index=INDEX_NAME,
    body={
        "mappings": {
            "properties": {
                "id": {"type": "keyword"},
                "genre": {"type": "keyword"},
                "artist": {"type": "text"},
                "name": {"type": "text"},
                "subgenres": {"type": "keyword"},
                "sad": {"type": "float"},
                "happy": {"type": "float"},
                "party": {"type": "float"},
                "popularity": {"type": "float"},
                "url": {"type": "keyword"},
                "embedding": {
                    "type": "dense_vector",
                    "dims": 768
                }
            }
        }
    }
)

/var/folders/6s/txq2rxns75g_2h8y8s20ttxw0000gn/T/ipykernel_3615/3135417993.py:3: DeprecationWarning: The 'http_auth' parameter is deprecated. Use 'basic_auth' or 'bearer_auth' parameters instead
  es = Elasticsearch(


ObjectApiResponse({'acknowledged': True, 'shards_acknowledged': True, 'index': 'music_embeddings'})

## 14. 💾 Insert Songs into Elasticsearch

Each song, along with its embedding and metadata, is inserted into an Elasticsearch index. The vector is stored using a `dense_vector` field type, while metadata like genre or artist is stored as standard fields for filtering.


In [77]:
# insert data into Elasticsearch
def generate_actions(data_set):
    for item in data_set:
        if item["embeddings"] is not None:
            index = item["index"]
            item_metadata = metadata.iloc[index]
            yield {
                "_index": INDEX_NAME,
                "_id": item["id"],
                "_source": {
                    "id": item["id"],
                    "genre": item_metadata["genre"],
                    "artist": item_metadata["artist"],
                    "name": item_metadata["name"],
                    "subgenres": item_metadata["subgenres"],
                    "sad": item_metadata["sad"],
                    "happy": item_metadata["happy"],
                    "party": item_metadata["party"],
                    "popularity": item_metadata["popularity"],
                    "url": item_metadata["url"],
                    "embedding": item["embeddings"]
                }
            }

helpers.bulk(es, generate_actions(data_set))

(520, [])

## 15. 🔍 Perform Hybrid Search (Vector + Metadata)

We perform a hybrid search query that combines:
- **Vector similarity** using the audio embedding.
- **Metadata filters** like genre, subgenre, or artist.

This enables flexible and intelligent discovery of similar songs based on both content and context.

In [79]:
def search_by_genre(genre: str, top_k: int = 5):
    query = {
        "query": {
            "match": {
                "genre": genre
            }
        },
        "size": top_k,
        "_source": ["id", "name", "artist", "url"]
    }
    
    response = es.search(index=INDEX_NAME, body=query)
    return response['hits']['hits']

# Example search
results = search_by_genre("rock", top_k=5)
results

[{'_index': 'music_embeddings',
  '_type': '_doc',
  '_id': '3zsUrcSjHX6d8DeIYyj1bE',
  '_score': 1.3843768,
  '_source': {'artist': 'The Jesus and Mary Chain',
   'name': 'Far Gone and Out',
   'id': '3zsUrcSjHX6d8DeIYyj1bE',
   'url': './../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/rock/3zsUrcSjHX6d8DeIYyj1bE.mp3'}},
 {'_index': 'music_embeddings',
  '_type': '_doc',
  '_id': '4NzcnIx2X1zq2DGVPdP8IY',
  '_score': 1.3843768,
  '_source': {'artist': 'Virus',
   'name': 'Shutout',
   'id': '4NzcnIx2X1zq2DGVPdP8IY',
   'url': './../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/rock/4NzcnIx2X1zq2DGVPdP8IY.mp3'}},
 {'_index': 'music_embeddings',
  '_type': '_doc',
  '_id': '5jZQJVYHgH01c5C3LMkxZ1',
  '_score': 1.3843768,
  '_source': {'artist': 'Melvins',
   'name': 'Missing',
   'id': '5jZQJVYHgH01c5C3LMkxZ1',
   'url': './../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/rock/5jZQJVYHgH01c5C3LMkxZ1.mp3'}},
 {'_index': 'music_embeddings',
  '_type': '_doc',
  '_

In [91]:
from IPython.display import Audio, display

# create a search by embedding function
def search_by_embedding(embedding: list, top_k: int = 5):
    query = {
        "size": top_k,
        "query": {
            "script_score": {
                "query": {"match_all": {}},
                "script": {
                    "source": "cosineSimilarity(params.query_vector, 'embedding') + 1.0",
                    "params": {"query_vector": embedding}
                }
            }
        },
        "_source": ["id", "name", "artist", "url"]
    }
    
    response = es.search(index=INDEX_NAME, body=query)
    return response['hits']['hits']

# Example search by embedding
print("Audio search by embedding example:")
display(Audio("../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/2a4807bsFF3T4m8vZVRRZs.mp3"))

print("Searching for similar audio tracks using embedding...")
example_embedding = get_audio_data("2a4807bsFF3T4m8vZVRRZs", "latin", model)["embeddings"]
results_by_embedding = search_by_embedding(example_embedding, top_k=5)

print("Results by embedding:")
for result in results_by_embedding:
    print(f"ID: {result['_source']['id']}, Name: {result['_source']['name']}, Artist: {result['_source']['artist']}")
    display(Audio(result['_source']['url']))


Audio search by embedding example:


Searching for similar audio tracks using embedding...
Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/2a4807bsFF3T4m8vZVRRZs.mp3 with shape (479818,)
Extracting embeddings from /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/2a4807bsFF3T4m8vZVRRZs.mp3...
With device: mps


Some weights of Wav2Vec2Model were not initialized from the model checkpoint at facebook/wav2vec2-base-960h and are newly initialized: ['masked_spec_embed']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/2a4807bsFF3T4m8vZVRRZs.mp3 with shape (479818,)
Audio tensor shape: (479818,)
Results by embedding:
ID: 39b7wKFIPHVdbTgUvEeKxu, Name: Campanera, Artist: Joselito
Results by embedding:
ID: 39b7wKFIPHVdbTgUvEeKxu, Name: Campanera, Artist: Joselito


ID: 6nmziSChpVSXk1Tc8UoWl3, Name: Desfigurado, Artist: Cartola


ID: 4N8mnAiP8GiTcGLr39Ry0S, Name: Tu sei, Artist: Eros Ramazzotti


ID: 1aUtScrWDFxlGGSChM2Gib, Name: Como?, Artist: Bebeto


ID: 5e7oIkcvyWHDTMvkMKCJnS, Name: Die Blume aus dem Gemeindebau, Artist: Wolfgang Ambros


In [ ]:
# hybrid search in elasticsearch 7.18


def hybrid_search(embedding: list, top_k: int = 5, terms: dict = None):
    """
    Perform a hybrid search using vector similarity and optional metadata term filters.

    Args:
        embedding (list): The query embedding vector.
        top_k (int): Number of results to return.
        terms (dict): Dictionary of field-value pairs for term filtering (e.g., {"genre": "pop", "artist": "Madonna"}).

    Returns:
        list: Search results from Elasticsearch.
    """
    filter_clauses = []
    if terms:
        for field, value in terms.items():
            filter_clauses.append({"term": {field: value}})
    query = {
        "size": top_k,
        "query": {
            "script_score": {
                "query": {"bool": {"filter": filter_clauses}} if filter_clauses else {"match_all": {}},
                "script": {
                    "source": "cosineSimilarity(params.query_vector, 'embedding') + 1.0",
                    "params": {"query_vector": embedding},
                },
            }
        },
        "_source": ["id", "name", "artist", "url", "genre"],
    }

    response = es.search(index=INDEX_NAME, body=query)
    return response["hits"]["hits"]

# Example hybrid search
print("Hybrid search example:")
display(Audio("../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/2a4807bsFF3T4m8vZVRRZs.mp3"))
example_embedding = get_audio_data("2a4807bsFF3T4m8vZVRRZs", "latin", model)["embeddings"]
results_hybrid = hybrid_search(example_embedding, top_k=5)
print("Results from hybrid search:")
for result in results_hybrid:
    print(f"ID: {result['_source']['id']}, Name: {result['_source']['name']}, Artist: {result['_source']['artist']}, Genre: {result['_source']['genre']}")
    display(Audio(result['_source']['url']))


Hybrid search example:


Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/2a4807bsFF3T4m8vZVRRZs.mp3 with shape (479818,)
Extracting embeddings from /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/2a4807bsFF3T4m8vZVRRZs.mp3...
With device: mps


Some weights of Wav2Vec2Model were not initialized from the model checkpoint at facebook/wav2vec2-base-960h and are newly initialized: ['masked_spec_embed']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loaded /Users/julian_castro/Documents/projects/audio_app/notebooks/utils/../../data/ludwig-music-dataset-moods-and-subgenres/mp3/mp3/latin/2a4807bsFF3T4m8vZVRRZs.mp3 with shape (479818,)
Audio tensor shape: (479818,)
Results from hybrid search:
ID: 4N8mnAiP8GiTcGLr39Ry0S, Name: Tu sei, Artist: Eros Ramazzotti, Genre: pop


ID: 5e7oIkcvyWHDTMvkMKCJnS, Name: Die Blume aus dem Gemeindebau, Artist: Wolfgang Ambros, Genre: pop


ID: 7A6CfD2sieeyrgiw3UUz5f, Name: Du kannst noch nicht mal richtig lügen, Artist: Andrea Berg, Genre: pop


ID: 2DvWVUrRXB0HYrjDqQWjjt, Name: The Sign (the remix), Artist: Ace of Base, Genre: pop


ID: 2OgD15H5DXlzgBGC92WPnd, Name: Rosy, Artist: Dick Annegarn, Genre: pop
